# MEDICAL INSURANCE CHARGES PREDICTION

***Importing Packages & Libraries***

In [1]:
import pyodbc
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')

***SQL SERVER Connectivity With Python*** 

In [2]:
conn = pyodbc.connect('Driver={ODBC Driver 17 for SQL Server};'
                      'Server=DESKTOP-U0EUVJ4;'
                      'Database=Medical_Insurance;'
                      'Trusted_Connection=yes;')
cursor=conn.cursor()

In [3]:
df = pd.read_sql("Select * from insurance",conn)
pd.set_option('display.max_columns', None)
df

age     sex     bmi children smoker     region      charges
0     19  female    27.9        0    yes  southwest    16884.924
1     18    male   33.77        1     no  southeast    1725.5523
2     28    male      33        3     no  southeast     4449.462
3     33    male  22.705        0     no  northwest  21984.47061
4     32    male   28.88        0     no  northwest    3866.8552
...   ..     ...     ...      ...    ...        ...          ...
1333  50    male   30.97        3     no  northwest   10600.5483
1334  18  female   31.92        0     no  northeast    2205.9808
1335  18  female   36.85        0     no  southeast    1629.8335
1336  21  female    25.8        0     no  southwest     2007.945
1337  61  female   29.07        0    yes  northwest   29141.3603

[1338 rows x 7 columns]

***Data Exploration***

Dataset consists of 1338 records. Each record contains the below data for specific person.

age – Age of the person

sex – Sex of the person

bmi – Body Mass Index(BMI) of the person

children – Number of children for the person

smoker – Smoking status of the person

region – Region of the person in US

charges – Medical Insurance costs per year for the person

***Copying original data into temporary dataset***

In [4]:
data = df.copy()

***Data Analysis Using Pandas Profiling***

In [5]:
from pandas_profiling import ProfileReport
profile = ProfileReport(data,title = "Pandas Profiling Report")
profile

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

****EDA(Exploratory Data Analysis)****

In [6]:
data.dtypes

age         object
sex         object
bmi         object
children    object
smoker      object
region      object
charges     object
dtype: object

In [7]:
data.isnull().sum()

age         0
sex         0
bmi         0
children    0
smoker      0
region      0
charges     0
dtype: int64

***Converting Data Types***

In [8]:
data['age'] = data['age'].astype(int, errors = 'raise')

In [9]:
data['bmi'] = data['bmi'].astype(float, errors = 'raise')

In [10]:
data['children'] = data['children'].astype(int, errors = 'raise')

In [11]:
data['charges'] = data['charges'].astype(float, errors = 'raise')

In [12]:
data.dtypes

age           int32
sex          object
bmi         float64
children      int32
smoker       object
region       object
charges     float64
dtype: object

In [13]:
## Here we will check the percentage of nan values present in each feature
## 1 - Making the list of features which has missing values
features_with_na=[features for features in data.columns if data[features].isnull().sum()>1]
## 2- Printing the feature name and the percentage of missing values

for feature in features_with_na:
    print(feature, np.round(data[feature].isnull().mean(), 4),  ' % missing values')

In [14]:
features_with_na

[]

In [15]:
# list of numerical variables
numerical_features = [feature for feature in data.columns if data[feature].dtypes != 'O']

print('Number of numerical variables: ', len(numerical_features))

# visualise the numerical variables
data[numerical_features].head()

Number of numerical variables:  4


age     bmi  children      charges
0   19  27.900         0  16884.92400
1   18  33.770         1   1725.55230
2   28  33.000         3   4449.46200
3   33  22.705         0  21984.47061
4   32  28.880         0   3866.85520

In [16]:
## Numerical variables are usually of 2 type
## 1. Continous variable and Discrete Variables

discrete_feature=[feature for feature in numerical_features if len(data[feature].unique())<25 ]
print("Discrete Variables Count: {}".format(len(discrete_feature)))

Discrete Variables Count: 1


In [17]:
discrete_feature

['children']

In [18]:
data.columns

Index(['age', 'sex', 'bmi', 'children', 'smoker', 'region', 'charges'], dtype='object')

In [19]:
data.head()

age     sex     bmi  children smoker     region      charges
0   19  female  27.900         0    yes  southwest  16884.92400
1   18    male  33.770         1     no  southeast   1725.55230
2   28    male  33.000         3     no  southeast   4449.46200
3   33    male  22.705         0     no  northwest  21984.47061
4   32    male  28.880         0     no  northwest   3866.85520

In [20]:
## Lets Find the realtionship between children and charges

for feature in discrete_feature:
    data=data.copy()
    data.groupby(feature)['charges'].median().plot.bar()
    plt.xlabel(feature)
    plt.ylabel('charges')
    plt.title(feature)
    plt.show()

In [21]:
data.head()

age     sex     bmi  children smoker     region      charges
0   19  female  27.900         0    yes  southwest  16884.92400
1   18    male  33.770         1     no  southeast   1725.55230
2   28    male  33.000         3     no  southeast   4449.46200
3   33    male  22.705         0     no  northwest  21984.47061
4   32    male  28.880         0     no  northwest   3866.85520

In [22]:
#Continous Variable
continuous_feature=[feature for feature in numerical_features if feature not in discrete_feature]
print("Continuous feature Count {}".format(len(continuous_feature)))

Continuous feature Count 3


In [23]:
continuous_feature

['age', 'bmi', 'charges']

In [24]:
## Lets analyse the continuous values by creating histograms to understand the distribution

for feature in continuous_feature:
    data=data.copy()
    data[feature].hist(bins=25)
    plt.xlabel(feature)
    plt.ylabel("Count")
    plt.title(feature)
    plt.show()

In [25]:
data.head()

age     sex     bmi  children smoker     region      charges
0   19  female  27.900         0    yes  southwest  16884.92400
1   18    male  33.770         1     no  southeast   1725.55230
2   28    male  33.000         3     no  southeast   4449.46200
3   33    male  22.705         0     no  northwest  21984.47061
4   32    male  28.880         0     no  northwest   3866.85520

In [26]:
#Categorical Featues

categorical_features=[feature for feature in data.columns if data[feature].dtypes=='O']
categorical_features

['sex', 'smoker', 'region']

In [27]:
for feature in categorical_features:
    print('The feature is {} and number of categories are {}'.format(feature,len(data[feature].unique())))

The feature is sex and number of categories are 2
The feature is smoker and number of categories are 2
The feature is region and number of categories are 4


In [28]:
## Find out the relationship between categorical variable and dependent feature
for feature in categorical_features:
    data=data.copy()
    data.groupby(feature)['charges'].median().plot.bar()
    plt.xlabel(feature)
    plt.ylabel('charges')
    plt.title(feature)
    plt.show()

***Feature Engineering***

***Handling Categorical Data***

In [29]:
from sklearn.preprocessing import LabelEncoder
le=LabelEncoder()

In [30]:
data['sex'] = le.fit_transform(data['sex'])

In [31]:
data['smoker'] = le.fit_transform(data['smoker'])

In [32]:
#data['region'] = le.fit_transform(data['region'])
# Airline vs Price
sns.catplot(y = "charges", x = "region", data =data.sort_values("charges", ascending = False), kind="boxen", height = 6, aspect = 3)
plt.show()

In [33]:
data['region'] = le.fit_transform(data['region'])

In [38]:
data.head()

age  sex     bmi  children  smoker  region      charges
0   19    0  27.900         0       1       3  16884.92400
1   18    1  33.770         1       0       2   1725.55230
2   28    1  33.000         3       0       2   4449.46200
3   33    1  22.705         0       0       1  21984.47061
4   32    1  28.880         0       0       1   3866.85520

In [39]:
from sklearn.model_selection import train_test_split
from sklearn import metrics
from pandas.plotting import scatter_matrix

In [40]:
X=data.drop(columns=['charges'])
X.head()

age  sex     bmi  children  smoker  region
0   19    0  27.900         0       1       3
1   18    1  33.770         1       0       2
2   28    1  33.000         3       0       2
3   33    1  22.705         0       0       1
4   32    1  28.880         0       0       1

In [41]:
X.shape

(1338, 6)

In [42]:
Y=data['charges']

In [43]:
Y.head()

0    16884.92400
1     1725.55230
2     4449.46200
3    21984.47061
4     3866.85520
Name: charges, dtype: float64

In [44]:
Y.shape

(1338,)

In [45]:
from sklearn.model_selection import train_test_split

In [46]:
x_train, x_test, y_train, y_test = train_test_split(X , Y , test_size = 0.2 , random_state = 42)

In [47]:
x_train.shape

(1070, 6)

In [48]:
x_test.shape

(268, 6)

In [49]:
y_train.shape

(1070,)

In [50]:
y_test.shape

(268,)

In [51]:
y_test

764      9095.06825
887      5272.17580
890     29330.98315
1293     9301.89355
259     33750.29180
           ...     
109     47055.53210
575     12222.89830
535      6067.12675
543     63770.42801
846      9872.70100
Name: charges, Length: 268, dtype: float64

In [52]:
from sklearn.linear_model import LinearRegression
lr= LinearRegression(normalize = True)

In [53]:
lr.fit(x_train,y_train)

LinearRegression(normalize=True)

In [54]:
lr.score(x_train,y_train)

0.7417049283233981

In [55]:
Y_pred_lr=lr.predict(x_test)

In [56]:
from sklearn.metrics import r2_score, mean_absolute_error, mean_squared_error

In [57]:
linear_score=metrics.r2_score(y_test,Y_pred_lr)
print(linear_score)
linear_mean_absolute_error=metrics.mean_absolute_error(y_test,Y_pred_lr)
print(linear_mean_absolute_error)
print(np.sqrt(mean_squared_error(y_test,Y_pred_lr)))

0.7833463107364536
4186.508898366437
5799.5870914383595


In [58]:
from sklearn.ensemble import RandomForestRegressor
rf= RandomForestRegressor(n_estimators=1000,min_samples_split = 10,max_depth = 10,min_samples_leaf = 5,n_jobs=4)

In [59]:
rf.fit(x_train,y_train)

RandomForestRegressor(max_depth=10, min_samples_leaf=5, min_samples_split=10,
                      n_estimators=1000, n_jobs=4)

In [60]:
rf.score(x_train,y_train)

0.9064491317694745

In [61]:
Y_pred_rf= rf.predict(x_test)

In [62]:
rf_score = metrics.r2_score(y_test,Y_pred_rf)
print(rf_score)
rf_mean_absolute_error=metrics.mean_absolute_error(y_test,Y_pred_rf)
print(rf_mean_absolute_error)
print(np.sqrt(mean_squared_error(y_test,Y_pred_rf)))

0.8789270833461773
2416.998970796091
4335.483448073028


In [63]:
#Hyperparameter Tuning on RandomForest
from sklearn.model_selection import RandomizedSearchCV

In [64]:
#Randomized Search CV

# Number of trees in random forest
n_estimators = [int(x) for x in np.linspace(start = 100, stop = 1200, num = 12)]
# Number of features to consider at every split
max_features = ['auto', 'sqrt']
# Maximum number of levels in tree
max_depth = [int(x) for x in np.linspace(5, 30, num = 6)]
# Minimum number of samples required to split a node
min_samples_split = [2, 5, 10, 15, 100]
# Minimum number of samples required at each leaf node
min_samples_leaf = [1, 2, 5, 10]

In [65]:
# Create the random grid

random_grid = {'n_estimators': n_estimators,
               'max_features': max_features,
               'max_depth': max_depth,
               'min_samples_split': min_samples_split,
               'min_samples_leaf': min_samples_leaf}

In [66]:
# Random search of parameters, using 5 fold cross validation, 
# search across 100 different combinations
rf_random = RandomizedSearchCV(estimator = rf, param_distributions = random_grid,scoring='neg_mean_squared_error', n_iter = 10, cv = 5, verbose=2, random_state=42, n_jobs = 1)

In [67]:
rf_random.fit(x_train,y_train)

Fitting 5 folds for each of 10 candidates, totalling 50 fits
[CV] END max_depth=10, max_features=sqrt, min_samples_leaf=5, min_samples_split=5, n_estimators=900; total time=  13.5s
[CV] END max_depth=10, max_features=sqrt, min_samples_leaf=5, min_samples_split=5, n_estimators=900; total time=   4.5s
[CV] END max_depth=10, max_features=sqrt, min_samples_leaf=5, min_samples_split=5, n_estimators=900; total time=   3.2s
[CV] END max_depth=10, max_features=sqrt, min_samples_leaf=5, min_samples_split=5, n_estimators=900; total time=   3.6s
[CV] END max_depth=10, max_features=sqrt, min_samples_leaf=5, min_samples_split=5, n_estimators=900; total time=   3.2s
[CV] END max_depth=15, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=1100; total time=   3.4s
[CV] END max_depth=15, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimators=1100; total time=   3.8s
[CV] END max_depth=15, max_features=sqrt, min_samples_leaf=2, min_samples_split=10, n_estimator

RandomizedSearchCV(cv=5,
                   estimator=RandomForestRegressor(max_depth=10,
                                                   min_samples_leaf=5,
                                                   min_samples_split=10,
                                                   n_estimators=1000,
                                                   n_jobs=4),
                   n_jobs=1,
                   param_distributions={'max_depth': [5, 10, 15, 20, 25, 30],
                                        'max_features': ['auto', 'sqrt'],
                                        'min_samples_leaf': [1, 2, 5, 10],
                                        'min_samples_split': [2, 5, 10, 15,
                                                              100],
                                        'n_estimators': [100, 200, 300, 400,
                                                         500, 600, 700, 800,
                                                         900, 1000, 1100,
      

In [68]:
rf_random.best_params_

{'n_estimators': 700,
 'min_samples_split': 5,
 'min_samples_leaf': 10,
 'max_features': 'auto',
 'max_depth': 20}

In [69]:
rf_new = RandomForestRegressor(n_estimators=700,min_samples_split=5,min_samples_leaf=10,max_features='auto',max_depth=20)

In [70]:
rf_new.fit(x_train,y_train)

RandomForestRegressor(max_depth=20, min_samples_leaf=10, min_samples_split=5,
                      n_estimators=700)

In [71]:
prediction = rf_new.predict(x_test)

In [72]:
rf.score(x_train,y_train)

0.9064491317694745

In [73]:
random_score = metrics.r2_score(y_test,prediction)
print(random_score)
random_mean_absolute_error = metrics.mean_absolute_error(y_test,prediction)
print(random_mean_absolute_error)
print(np.sqrt(mean_squared_error(y_test,prediction)))

0.8790638955797287
2426.719215681051
4333.033210443207


In [74]:
#GradientBoostingRegressor

In [75]:
from sklearn.ensemble import GradientBoostingRegressor

In [76]:
gr = GradientBoostingRegressor()

In [77]:
gr.fit(x_train,y_train)

GradientBoostingRegressor()

In [78]:
gr.score(x_train,y_train)

0.8980459663933704

In [79]:
Y_pred_gr= gr.predict(x_test)

In [80]:
gr_score=metrics.r2_score(y_test,Y_pred_gr)
print(gr_score)
gr_mean_absolute_error=metrics.mean_absolute_error(y_test,Y_pred_gr)
print(gr_mean_absolute_error)
print(np.sqrt(mean_squared_error(y_test,Y_pred_gr)))

0.8779726251291786
2447.9515580545844
4352.538932159728


In [81]:
df2 = pd.DataFrame({'Actual':y_test,'Linear':Y_pred_lr,'Random_forest':prediction,'Gradient':Y_pred_gr})

In [82]:
df2

Actual        Linear  Random_forest      Gradient
764    9095.06825   8924.407244   10615.951183  11001.128629
887    5272.17580   7116.295018    5339.392491   5840.174656
890   29330.98315  36909.013521   27220.706101  28001.980112
1293   9301.89355   9507.874691   10491.271498   9745.291602
259   33750.29180  27013.350008   34917.908211  33639.100981
...           ...           ...            ...           ...
109   47055.53210  39116.968669   47151.471762  45431.423211
575   12222.89830  11814.555568   12631.181075  12465.025294
535    6067.12675   7638.107736    6801.836795   6974.336525
543   63770.42801  40959.081722   46958.751700  47862.047791
846    9872.70100  12258.228529    9908.714339  10289.655388

[268 rows x 4 columns]

In [83]:
plt.figure(figsize=(20,10))
plt.subplot()
plt.plot(df2['Actual'],label='Actual')
plt.plot(df2['Random_forest'],label='Random_forest')
plt.legend()

In [84]:
df2[['Actual','Random_forest']].head(50)

Actual  Random_forest
764    9095.06825   10615.951183
887    5272.17580    5339.392491
890   29330.98315   27220.706101
1293   9301.89355   10491.271498
259   33750.29180   34917.908211
1312   4536.25900    6824.003091
899    2117.33885    2121.307864
752   14210.53595   14292.885268
1286   3732.62510    5592.075649
707   10264.44210   11438.571034
780   18259.21600   19046.143967
567    7256.72310    7892.698818
76     3947.41310    4672.120221
265   46151.12450   45345.741483
901   48673.55880   47617.181726
893   44202.65360   45358.246340
650    9800.88820   10410.803789
615   42969.85270   45155.420196
538    8233.09750   10250.689763
916   21774.32215   25410.031284
413    5080.09600    5219.574467
598    7441.50100    8884.212179
513    1256.29900    2131.430589
78     2755.02095    3628.505316
1135  11085.58680   12088.968092
561   10923.93320   12777.633307
904   12644.58900   13914.403919
429   18804.75240    7202.256715
275    9715.84100   11929.508964
808    1131.50660    2308.723775
1253  15828.82173    7818.942897
765   11842.62375   12535.971200
700    2020.55230    2889.616420
1119   5693.43050    6778.470076
1108   2904.08800    3606.893056
777    7448.40395   10695.847530
363    2597.77900    3097.309973
1263   7337.74800    8243.029557
1176  23887.66270   23915.665986
49    38709.17600   40944.908694
32     4687.79700    5005.416810
506    2643.26850    4838.281794
945   11674.13000   12574.147118
1015  12124.99240   14258.468590
346    4889.99950    6784.289683
233   12333.82800   15769.380110
51     3579.82870    8479.889425
869    4391.65200    5219.966929
312   42124.51530   43379.735821
237    4463.20510    5794.414984

In [85]:
print(linear_score,random_score,gr_score)

0.7833463107364536 0.8790638955797287 0.8779726251291786


In [86]:
print(linear_mean_absolute_error,random_mean_absolute_error,gr_mean_absolute_error)

4186.508898366437 2426.719215681051 2447.9515580545844


In [87]:
dataset1 = pd.DataFrame(prediction,columns=['Predicted_Charges'])
dataset1.head()

Predicted_Charges
0       10615.951183
1        5339.392491
2       27220.706101
3       10491.271498
4       34917.908211

In [88]:
train_prediction = rf_new.predict(x_train)

In [89]:
dataset2 = pd.DataFrame(train_prediction,columns=['Predicted_Charges'])
dataset2.head()

Predicted_Charges
0        9745.915239
1       11052.907361
2       13326.920251
3        8410.677929
4       13652.057691

In [90]:
dataset1.shape

(268, 1)

In [91]:
dataset2.shape

(1070, 1)

In [92]:
data.shape

(1338, 7)

In [93]:
dataset3 = pd.concat([dataset2,dataset1], ignore_index=True, sort=False)

In [94]:
dataframe = pd.concat([data,dataset3],axis=1)
dataframe.shape

(1338, 8)

In [95]:
df.head()

age     sex     bmi children smoker     region      charges
0  19  female    27.9        0    yes  southwest    16884.924
1  18    male   33.77        1     no  southeast    1725.5523
2  28    male      33        3     no  southeast     4449.462
3  33    male  22.705        0     no  northwest  21984.47061
4  32    male   28.88        0     no  northwest    3866.8552

In [96]:
X.head()

age  sex     bmi  children  smoker  region
0   19    0  27.900         0       1       3
1   18    1  33.770         1       0       2
2   28    1  33.000         3       0       2
3   33    1  22.705         0       0       1
4   32    1  28.880         0       0       1

In [97]:
gr.predict([[19,0,27.900,0,1,3],[18,1,33.770,1,0,2],[28,1,33.000,3,0,2],[32,1,28.880,0,0,1]])

array([17792.46608893,  3568.57433305,  6242.07890386,  4206.17630525])

In [98]:
dataframe.to_csv('modified.csv',index=False)
dataframe.head()

age  sex     bmi  children  smoker  region      charges  Predicted_Charges
0   19    0  27.900         0       1       3  16884.92400        9745.915239
1   18    1  33.770         1       0       2   1725.55230       11052.907361
2   28    1  33.000         3       0       2   4449.46200       13326.920251
3   33    1  22.705         0       0       1  21984.47061        8410.677929
4   32    1  28.880         0       0       1   3866.85520       13652.057691

In [99]:
df2=pd.read_csv("modified.csv")

In [100]:
cursor.execute('create table predicted_charges (age varchar(50),sex varchar(50),bmi varchar(50),children varchar(50),smoker varchar(50),region varchar(50),charges varchar(50),Predicted_Charges varchar(50))')

In [101]:
for row in df2.itertuples():
    cursor.execute('''
                  insert into Medical_Insurance.dbo.predicted_charges (age,sex,bmi,children,smoker,region,charges,Predicted_Charges)
                  values(?,?,?,?,?,?,?,?)
                  ''',
                  row.age,
                  row.sex,
                  row.bmi,
                  row.children,
                  row.smoker,
                  row.region,
                  row.charges,
                  row.Predicted_Charges  
                  )
conn.commit()

In [102]:
df3 = pd.read_sql("Select * from predicted_charges",conn)
pd.set_option('display.max_columns', None)
df3

age sex     bmi children smoker region  charges Predicted_Charges
0     19   0    27.9        0      1      3  16884.9           9745.92
1     18   1   33.77        1      0      2  1725.55           11052.9
2     28   1      33        3      0      2  4449.46           13326.9
3     33   1  22.705        0      0      1  21984.5           8410.68
4     32   1   28.88        0      0      1  3866.86           13652.1
...   ..  ..     ...      ...    ...    ...      ...               ...
1333  50   1   30.97        3      0      1  10600.5           47151.5
1334  18   0   31.92        0      0      0  2205.98           12631.2
1335  18   0   36.85        0      0      2  1629.83           6801.84
1336  21   0    25.8        0      0      3  2007.94           46958.8
1337  61   0   29.07        0      1      1  29141.4           9908.71

[1338 rows x 8 columns]

# Saving model to reuse it again

In [106]:
import pickle
# open a file, where we want to store the data
file = open('pred_price.pkl', 'wb')

In [107]:
# dumping information to that file
pickle.dump(rf_new, file)

In [108]:
model = open('pred_price.pkl','rb')
forest = pickle.load(model)

In [109]:
y_prediction = forest.predict(x_test)

In [110]:
from sklearn import metrics
metrics.r2_score(y_test, y_prediction)

0.8790638955797287